# Introduction

In this analysis, the problem will be picking up the best neighborhood for pet owners.
The definition of the best neighborhood is based on the number of veterarian/pet clinics,pet store,Pet Café and pet services provider.
The audience for this analysis will be pet owners who are looking for a good neighborhood to move in.

# Data

### Data source 1: Foursquare 
This will provide the data part for veterarian and ratings.
The structure will come with the Venue Name, Venue Category.

### Data source 2: Previouse New York Neighborhood Data
City: NY, United States   
I will leverage the data from the labs in previous weeks for New York city.
Data structure neighborhood name, borough, latitude, and longtitude.


## Methodology

We will first explore each datasource and clean up the dataset and make them into data frame. 
Then we will combine the data set so that the neighborhoods, latitutde, and longtitude could have the information about venues, and categories. 

Then, I will filter out the neighborhoods that has the venue category in pet-related services. 

Finally, we will run a k-means on the data set to get the clusters. Then we can examine each cluster and make recommendations.

## Analysis Part
Now let's get started! 
First, we will have to import all the libraries.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [2]:
#Let's download the new york data provided by the previous week Lab session.

!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
#Now let's open the json file
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
#Take a look at the data
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
#Now let's get the feature out of the json file. This is the first step that allow us the retreive the neighborhood data
neighborhoods_data = newyork_data['features']
#Let's take a look at one element. So we need the coordinates which are the latitutde and longtitude, Borogh, Neighborhood name.
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [6]:
# Transfer the json file into a pandas data frame
# let's create a data frame with column names first
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [7]:
#Now we will be filling in the data frame one row each time
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [8]:
#So we get the dataframe with Borough, neighborhood, latitutde and longtitude
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [9]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


### So to this point, we have already get the data source 2 done. Next, we will need to get the data source 1 which is foursquare data.

In [10]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7308619, -73.9871558.


### Let's visualize the neighborhoods on the map first.

In [11]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

### Now, let's use the foursquare API to retrieve the data to explore the neighborhoods and find the best one for our pet owners.

In [12]:
CLIENT_ID = '32XWTEAZI4KELYE1KZLWYS2UBS0B2DERB2VWGFJDC0SNF10K' # your Foursquare ID
CLIENT_SECRET = 'DQPXJDNIQCKQEW1A5K14CWADMW4U1IAXOIRVO1RF3YJVFOMC' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 32XWTEAZI4KELYE1KZLWYS2UBS0B2DERB2VWGFJDC0SNF10K
CLIENT_SECRET:DQPXJDNIQCKQEW1A5K14CWADMW4U1IAXOIRVO1RF3YJVFOMC


### Now let's get the 2500 venues in New York city within 1000 meters.

In [13]:
LIMIT = 2000
radius = 3000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=32XWTEAZI4KELYE1KZLWYS2UBS0B2DERB2VWGFJDC0SNF10K&client_secret=DQPXJDNIQCKQEW1A5K14CWADMW4U1IAXOIRVO1RF3YJVFOMC&v=20180605&ll=40.7308619,-73.9871558&radius=3000&limit=2000'

### Now, let's examine the results

In [14]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c5efc22351e3d1951e703ce'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'New York',
  'headerFullLocation': 'New York',
  'headerLocationGranularity': 'city',
  'totalResults': 236,
  'suggestedBounds': {'ne': {'lat': 40.75786192700003,
    'lng': -73.9515920362125},
   'sw': {'lat': 40.70386187299997, 'lng': -74.02271956378749}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '3fd66200f964a5203de41ee3',
       'name': 'Sake Bar Decibel',
       'location': {'address': '240 E 9th St',
        'crossStreet': 'btwn 2nd & 3rd Ave.',
        'lat': 40.72941823593811,
        'lng': -73.98776923605922,
     

### We could see that there's categories in the results, which are very important to us. So let's extract them and transform them into dataframe.

In [15]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [16]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng','venue.location.address','venue.city','venue.state']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

values = {'city': 'New York', 'state': 'NY'}
nearby_venues.fillna(value=values,inplace=True)
nearby_venues


/Users/Cykie/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


name                     categories  \
0                             Sake Bar Decibel                       Sake Bar   
1                            Momofuku Ssäm Bar               Asian Restaurant   
2                                Angel’s Share                      Speakeasy   
3                                  Shake Shack                   Burger Joint   
4                     Peridance Capezio Center                   Dance Studio   
5                                       Ippudo               Ramen Restaurant   
6                           Yoga to the People                    Yoga Studio   
7                       Trader Joe's Wine Shop                      Wine Shop   
8                               Juice Vitality                      Juice Bar   
9                Van Leeuwen Artisan Ice Cream                 Ice Cream Shop   
10                            Taverna Kyclades               Greek Restaurant   
11                            Strand Bookstore                      Bookstore   
12                          Mighty Quinn's BBQ                      BBQ Joint   
13                            Elf Cosmetics HQ                 Cosmetics Shop   
14                          The Public Theater                        Theater   
15                                Cafe Mogador            Moroccan Restaurant   
16                               Good Beer NYC                     Beer Store   
17                       Barry's Bootcamp NoHo                            Gym   
18           Upstate Craft Beer and Oyster Bar             Seafood Restaurant   
19                           Union Square Park                           Park   
20                                Emmy Squared                    Pizza Place   
21                                        Kura            Japanese Restaurant   
22                       Astor Wines & Spirits                      Wine Shop   
23                                 Dear Irving                   Cocktail Bar   
24                                   Yoga Vida                    Yoga Studio   
25                              Miss Lily's 7A           Caribbean Restaurant   
26                            The Bowery Hotel                          Hotel   
27                         Bedford Cheese Shop                    Cheese Shop   
28                    Union Square Greenmarket                 Farmers Market   
29                                 Fish Cheeks                Thai Restaurant   
30                            MNDFL Meditation               Spiritual Center   
31                                     Il Buco             Italian Restaurant   
32                              Dashwood Books                      Bookstore   
33                            Daily Provisions                           Café   
34                               Breads Bakery                         Bakery   
35                                   Haven Spa                            Spa   
36                                 ABC Kitchen        New American Restaurant   
37                        Overthrow Boxing NYC                     Boxing Gym   
38                              Champion Pizza                    Pizza Place   
39                  Sunny & Annie Gourmet Deli                  Deli / Bodega   
40                      Washington Square Park                           Park   
41                             Gramercy Tavern            American Restaurant   
42                                    Maialino             Italian Restaurant   
43                                  sweetgreen                    Salad Place   
44                                  Fishs Eddy         Furniture / Home Store   
45                            Russ & Daughters                   Gourmet Shop   
46                   Stumptown Coffee Roasters                    Coffee Shop   
47                   Washington Square Dog Run                        Dog Run   
48                                  Thai Villa                Thai Restau

In [17]:
#I am concatinate three variables to create a full address
nearby_venues['Address'] = nearby_venues['address'].map(str) + ',' + nearby_venues['city'].map(str) + ',' + nearby_venues['state'].map(str)

In [18]:
#Now we could drop the three variables and just leave the full address in the data frame.
nearby_venues.drop(['address','city','state'],axis=1,inplace=True)
nearby_venues

name                     categories  \
0                             Sake Bar Decibel                       Sake Bar   
1                            Momofuku Ssäm Bar               Asian Restaurant   
2                                Angel’s Share                      Speakeasy   
3                                  Shake Shack                   Burger Joint   
4                     Peridance Capezio Center                   Dance Studio   
5                                       Ippudo               Ramen Restaurant   
6                           Yoga to the People                    Yoga Studio   
7                       Trader Joe's Wine Shop                      Wine Shop   
8                               Juice Vitality                      Juice Bar   
9                Van Leeuwen Artisan Ice Cream                 Ice Cream Shop   
10                            Taverna Kyclades               Greek Restaurant   
11                            Strand Bookstore                      Bookstore   
12                          Mighty Quinn's BBQ                      BBQ Joint   
13                            Elf Cosmetics HQ                 Cosmetics Shop   
14                          The Public Theater                        Theater   
15                                Cafe Mogador            Moroccan Restaurant   
16                               Good Beer NYC                     Beer Store   
17                       Barry's Bootcamp NoHo                            Gym   
18           Upstate Craft Beer and Oyster Bar             Seafood Restaurant   
19                           Union Square Park                           Park   
20                                Emmy Squared                    Pizza Place   
21                                        Kura            Japanese Restaurant   
22                       Astor Wines & Spirits                      Wine Shop   
23                                 Dear Irving                   Cocktail Bar   
24                                   Yoga Vida                    Yoga Studio   
25                              Miss Lily's 7A           Caribbean Restaurant   
26                            The Bowery Hotel                          Hotel   
27                         Bedford Cheese Shop                    Cheese Shop   
28                    Union Square Greenmarket                 Farmers Market   
29                                 Fish Cheeks                Thai Restaurant   
30                            MNDFL Meditation               Spiritual Center   
31                                     Il Buco             Italian Restaurant   
32                              Dashwood Books                      Bookstore   
33                            Daily Provisions                           Café   
34                               Breads Bakery                         Bakery   
35                                   Haven Spa                            Spa   
36                                 ABC Kitchen        New American Restaurant   
37                        Overthrow Boxing NYC                     Boxing Gym   
38                              Champion Pizza                    Pizza Place   
39                  Sunny & Annie Gourmet Deli                  Deli / Bodega   
40                      Washington Square Park                           Park   
41                             Gramercy Tavern            American Restaurant   
42                                    Maialino             Italian Restaurant   
43                                  sweetgreen                    Salad Place   
44                                  Fishs Eddy         Furniture / Home Store   
45                            Russ & Daughters                   Gourmet Shop   
46                   Stumptown Coffee Roasters                    Coffee Shop   
47                   Washington Square Dog Run                        Dog Run   
48                                  Thai Villa                Thai Restau

In [19]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


### Now, let's combine the neighborhoods data with new york city venues data from foursquare.

In [23]:
def getNearbyVenues(names, latitudes, longitudes, radius=3000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues_clean = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues_clean.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues_clean)

In [24]:

nearby_venues_clean = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [25]:
print(nearby_venues_clean.shape)
nearby_venues_clean.head()

(29791, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                         Venue  Venue Latitude  Venue Longitude  \
0             Lollipops Gelato       40.894123       -73.845892   
1           Ripe Kitchen & Bar       40.898152       -73.838875   
2              Ali's Roti Shop       40.894036       -73.856935   
3  Jackie's West Indian Bakery       40.889283       -73.843310   
4     Kingston Tropical Bakery       40.888568       -73.859885   

         Venue Category  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3  Caribbean Restaurant  
4                Bakery

### Let's see how many venues each neighbood has.

In [27]:
nearby_venues_clean.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                     100                     100   
Annadale                                     100                     100   
Arden Heights                                100                     100   
Arlington                                    100                     100   
Arrochar                                     100                     100   
Arverne                                       55                      55   
Astoria                                      100                     100   
Astoria Heights                              100                     100   
Auburndale                                   100                     100   
Bath Beach                                   100                     100   
Battery Park City                            100                     100   
Bay Ridge                                    100                     100   
Bay Terrace                                  168                     168   
Baychester                                   100                     100   
Bayside                                      100                     100   
Bayswater                                     58                      58   
Bedford Park                                 100                     100   
Bedford Stuyvesant                           100                     100   
Beechhurst                                    97                      97   
Bellaire                                     100                     100   
Belle Harbor                                  74                      74   
Bellerose                                    100                     100   
Belmont                                      100                     100   
Bensonhurst                                  100                     100   
Bergen Beach                                 100                     100   
Blissville                                   100                     100   
Bloomfield                                   100                     100   
Boerum Hill                                  100                     100   
Borough Park                                 100                     100   
Breezy Point                                  22                      22   
Briarwood                                    100                     100   
Brighton Beach                               100                     100   
Broad Channel                                 54                      54   
Broadway Junction                            100                     100   
Bronxdale                                    100                     100   
Brooklyn Heights                             100                     100   
Brookville                                   100                     100   
Brownsville                                  100                     100   
Bulls Head                                   100                     100   
Bushwick                                     100                     100   
Butler Manor                                  83                      83   
Cambria Heights                              100                     100   
Canarsie                                     100                     100   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                  100                     100   
Castleton Corners                            100                     100   
Central Harlem                               100                     100   
Charleston                                   100                     100   
Chelsea                                      200                     200   
Chinatown                                    100                     100   

### Let's use the onehot group to transform the dataframe

In [28]:
# one hot encoding
ny_onehot = pd.get_dummies(nearby_venues_clean[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = nearby_venues_clean['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Zoo Exhibit  Accessories Store  Afghan Restaurant  African Restaurant  \
0            0                  0                  0                   0   
1            0                  0                  0                   0   
2            0                  0                  0                   0   
3            0                  0                  0                   0   
4            0                  0                  0                   0   

   Airport Food Court  Airport Lounge  American Restaurant  Amphitheater  \
0                   0               0                    0             0   
1                   0               0                    0             0   
2                   0               0                    0             0   
3                   0               0                    0             0   
4                   0               0                    0             0   

   Animal Shelter  Antique Shop  Aquarium  Arcade  Arepa Restaurant  \
0               0             0         0       0                 0   
1               0             0         0       0                 0   
2               0             0         0       0                 0   
3               0             0         0       0                 0   
4               0             0         0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Austrian Restaurant  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                    0                0          0           0       0     0   
1                    0                0          0           0       0     0   
2                    0                0          0           0       0     0   
3                    0                0          0           0       0     0   
4                    0                0          0           0       1     0   

   Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0    0               0                 0                 0   
1    0               0                 0                 0   
2    0               0                 0                 0   
3    0               0                 0                 0   
4    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0           0              0                         0   

   Bike Trail  Bistro  Board Shop  Boat 

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [29]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Zoo Exhibit  Accessories Store  \
0                     Allerton         0.01               0.00   
1                     Annadale         0.00               0.00   
2                Arden Heights         0.00               0.00   
3                    Arlington         0.00               0.03   
4                     Arrochar         0.00               0.00   
5                      Arverne         0.00               0.00   
6                      Astoria         0.00               0.00   
7              Astoria Heights         0.00               0.00   
8                   Auburndale         0.00               0.00   
9                   Bath Beach         0.00               0.00   
10           Battery Park City         0.00               0.00   
11                   Bay Ridge         0.00               0.00   
12                 Bay Terrace         0.00               0.00   
13                  Baychester         0.00               0.00   
14                     Bayside         0.00               0.00   
15                   Bayswater         0.00               0.00   
16                Bedford Park         0.00               0.00   
17          Bedford Stuyvesant         0.00               0.00   
18                  Beechhurst         0.00               0.00   
19                    Bellaire         0.00               0.00   
20                Belle Harbor         0.00               0.00   
21                   Bellerose         0.00               0.00   
22                     Belmont         0.02               0.00   
23                 Bensonhurst         0.00               0.00   
24                Bergen Beach         0.00               0.00   
25                  Blissville         0.00               0.00   
26                  Bloomfield         0.00               0.00   
27                 Boerum Hill         0.00               0.00   
28                Borough Park         0.00               0.00   
29                Breezy Point         0.00               0.00   
30                   Briarwood         0.00               0.00   
31              Brighton Beach         0.00               0.00   
32               Broad Channel         0.00               0.00   
33           Broadway Junction         0.00               0.00   
34                   Bronxdale         0.02               0.00   
35            Brooklyn Heights         0.00               0.00   
36                  Brookville         0.00               0.00   
37                 Brownsville         0.00               0.00   
38                  Bulls Head         0.00               0.00   
39                    Bushwick         0.00               0.00   
40                Butler Manor         0.00               0.00   
41             Cambria Heights         0.00               0.00   
42                    Canarsie         0.00               0.00   
43               Carnegie Hill         0.00               0.00   
44             Carroll Gardens         0.00               0.00   
45                 Castle Hill         0.00               0.00   
46           Castleton Corners         0.00               0.00   
47              Central Harlem         0.00               0.00   
48                  Charleston         0.00               0.00   
49                     Chelsea         0.00               0.00   
50                   Chinatown         0.00               0.00   
51                 City Island         0.00               0.00   
52                   City Line         0.00               0.00   
53                Civic Center         0.00               0.00   
54           Claremont Village         0.00               0.00   
55                Clason Point         0.00               0.00   
56                     Clifton         0.00               0.00   
57                     Clinton         0.00               0.00   
58                Clinton Hill         0.00               0.00   
59                  Co-op City         0.00               

### Next, we will only keep the neighborhood with the pet related services and remove the rest of neighborhoods that don't.

In [30]:
#Now, let's get the neighborhood with the pet related service.

ny_grouped_pet=ny_grouped.drop(ny_grouped[(ny_grouped['Veterinarian'] ==0) & (ny_grouped['Pet Store']== 0)& (ny_grouped['Pet Service']== 0)].index)
ny_grouped_pet

Neighborhood  Zoo Exhibit  Accessories Store  Afghan Restaurant  \
3               Arlington          0.0               0.03               0.00   
8              Auburndale          0.0               0.00               0.00   
18             Beechhurst          0.0               0.00               0.00   
28           Borough Park          0.0               0.00               0.00   
36             Brookville          0.0               0.00               0.00   
38             Bulls Head          0.0               0.00               0.00   
39               Bushwick          0.0               0.00               0.00   
40           Butler Manor          0.0               0.00               0.00   
42               Canarsie          0.0               0.00               0.00   
45            Castle Hill          0.0               0.00               0.00   
46      Castleton Corners          0.0               0.00               0.00   
48             Charleston          0.0               0.00               0.00   
49                Chelsea          0.0               0.00               0.00   
52              City Line          0.0               0.00               0.00   
55           Clason Point          0.0               0.00               0.00   
59             Co-op City          0.0               0.00               0.00   
61          College Point          0.0               0.00               0.00   
70            Ditmas Park          0.0               0.00               0.00   
72             Douglaston          0.0               0.00               0.00   
83            Eastchester          0.0               0.00               0.00   
84               Edenwald          0.0               0.00               0.00   
85               Edgemere          0.0               0.00               0.00   
88               Elm Park          0.0               0.00               0.00   
93           Far Rockaway          0.0               0.00               0.00   
96               Flatbush          0.0               0.00               0.00   
98              Flatlands          0.0               0.00               0.00   
100              Flushing          0.0               0.00               0.00   
103  Forest Hills Gardens          0.0               0.00               0.00   
107         Fresh Meadows          0.0               0.00               0.00   
110       Gerritsen Beach          0.0               0.00               0.00   
111             Glen Oaks          0.0               0.00               0.01   
112              Glendale          0.0               0.00               0.00   
115          Graniteville          0.0               0.00               0.00   
116            Grant City          0.0               0.00               0.00   
120            Greenpoint          0.0               0.00               0.00   
126     Heartland Village          0.0               0.00               0.00   
129             Hillcrest          0.0               0.00               0.01   
131            Holliswood          0.0               0.00               0.01   
132             Homecrest          0.0               0.00               0.00   
133          Howard Beach          0.0               0.00               0.00   
139                Inwood          0.0               0.00               0.00   
142       Jamaica Estates          0.0               0.00               0.00   
144            Kensington          0.0               0.00               0.00   
145           Kew Gardens          0.0               0.00               0.00   
147           Kingsbridge          0.0               0.00               0.00   
148   Kingsbridge Heights          0.0               0.00               0.00   
149             Laurelton          0.0               0.00               0.00   
154            Lindenwood          0.0               0.00               0.00   
156           Little Neck          0.0               0.00               0.00   
161          

### Let's print each neighborhood along with the top 5 most common venues

In [31]:
num_top_venues = 5

for hood in ny_grouped_pet['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped_pet[ny_grouped_pet['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arlington----
                 venue  freq
0       Clothing Store  0.16
1     Department Store  0.04
2       Ice Cream Shop  0.04
3    Accessories Store  0.03
4  American Restaurant  0.03


----Auburndale----
               venue  freq
0  Korean Restaurant  0.16
1         Bagel Shop  0.05
2   Greek Restaurant  0.04
3  Indian Restaurant  0.04
4        Pizza Place  0.03


----Beechhurst----
                venue  freq
0       Deli / Bodega  0.07
1  Italian Restaurant  0.06
2                Park  0.06
3         Pizza Place  0.06
4          Donut Shop  0.04


----Borough Park----
                venue  freq
0         Pizza Place  0.08
1  Mexican Restaurant  0.07
2                Café  0.06
3     Thai Restaurant  0.04
4         Coffee Shop  0.04


----Brookville----
                  venue  freq
0  Caribbean Restaurant  0.12
1            Donut Shop  0.05
2        Clothing Store  0.05
3                  Park  0.04
4        Discount Store  0.04


----Bulls Head----
                venue  

                venue  freq
0         Pizza Place  0.11
1  Italian Restaurant  0.07
2      Discount Store  0.05
3         Supermarket  0.04
4      Ice Cream Shop  0.04


----Little Neck----
                venue  freq
0         Pizza Place  0.07
1  Italian Restaurant  0.05
2       Grocery Store  0.04
3  Chinese Restaurant  0.03
4    Greek Restaurant  0.03


----Malba----
                venue  freq
0         Pizza Place  0.09
1       Deli / Bodega  0.08
2                Park  0.06
3   Korean Restaurant  0.05
4  Italian Restaurant  0.04


----Manhattan Beach----
              venue  freq
0  Sushi Restaurant  0.06
1             Beach  0.05
2        Restaurant  0.05
3    Sandwich Place  0.04
4       Pizza Place  0.04


----Manor Heights----
                 venue  freq
0   Italian Restaurant  0.09
1          Pizza Place  0.09
2    Convenience Store  0.06
3  American Restaurant  0.05
4       Sandwich Place  0.03


----Marble Hill----
                       venue  freq
0         Mexican Res

                 venue  freq
0          Pizza Place  0.08
1           Bagel Shop  0.06
2   Chinese Restaurant  0.05
3  American Restaurant  0.05
4   Italian Restaurant  0.04


----Woodhaven----
                 venue  freq
0          Pizza Place  0.14
1                Diner  0.04
2       Ice Cream Shop  0.03
3  Japanese Restaurant  0.03
4                  Gym  0.03




### Let's put the top venue into pandas dataframe so later we could simply merge it with our vet group data frame.

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [33]:
## Instead of top 5 venue, let's put top 10 into the data frame
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = ny_grouped_pet['Neighborhood']

for ind in np.arange(ny_grouped_pet.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped_pet.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3      Arlington        Clothing Store        Ice Cream Shop   
8     Auburndale     Korean Restaurant            Bagel Shop   
18    Beechhurst         Deli / Bodega    Italian Restaurant   
28  Borough Park           Pizza Place    Mexican Restaurant   
36    Brookville  Caribbean Restaurant        Clothing Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3       Department Store   Sporting Goods Shop     Accessories Store   
8       Greek Restaurant     Indian Restaurant           Pizza Place   
18                  Park           Pizza Place            Donut Shop   
28                  Café       Thai Restaurant           Coffee Shop   
36            Donut Shop        Discount Store                  Park   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3              Pizza Place   American Restaurant         Shopping Mall   
8           Ice Cream Shop                Bakery              Pharmacy   
18                  Bakery        Cosmetics Shop            Bagel Shop   
28      Italian Restaurant    Chinese Restaurant                   Bar   
36  Furniture / Home Store        Sandwich Place              Pharmacy   

   9th Most Common Venue 10th Most Common Venue  
3            Men's Store       Toy / Game Store  
8           Liquor Store                   Park  
18     Martial Arts Dojo   Gym / Fitness Center  
28                Bakery               Tea Room  
36           Pizza Place         Cosmetics Shop

### Now, let's continue with the K-means cluster

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [34]:
kclusters = 3

ny_grouped_clustering = ny_grouped_pet.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 1, 0, 2, 1, 2, 0, 1], dtype=int32)

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = neighborhoods

In [36]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
ny_merged = ny_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

ny_merged.head() # check the last columns!


Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             0.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             0.0   
3   Bronx    Fieldston  40.895437 -73.905643             NaN   
4   Bronx    Riverdale  40.890834 -73.912585             1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Caribbean Restaurant           Pizza Place              Pharmacy   
1  Caribbean Restaurant           Pizza Place                Bakery   
2  Caribbean Restaurant              Pharmacy           Pizza Place   
3                   NaN                   NaN                   NaN   
4           Pizza Place    Mexican Restaurant           Coffee Shop   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                Bakery                 Diner                   Gym   
1         Grocery Store        Discount Store              Pharmacy   
2                Bakery        Discount Store                 Diner   
3                   NaN                   NaN                   NaN   
4                  Café                  Park                Bakery   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop          Burger Joint    Seafood Restaurant   
1  Fast Food Restaurant    Italian Restaurant    Seafood Restaurant   
2         Grocery Store          Burger Joint         Shopping Mall   
3                   NaN                   NaN                   NaN   
4                 Diner             Wine Shop          Burger Joint   

   10th Most Common Venue  
0      Italian Restaurant  
1    Gym / Fitness Center  
2  Furniture / Home Store  
3                     NaN  
4          Scenic Lookout

In [37]:
ny_merged = ny_merged[pd.notnull(ny_merged['Cluster Labels'])]
ny_merged['Cluster Labels'] = ny_merged['Cluster Labels'].astype(int)
ny_merged.head()

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               0   
1   Bronx   Co-op City  40.874294 -73.829939               0   
2   Bronx  Eastchester  40.887556 -73.827806               0   
4   Bronx    Riverdale  40.890834 -73.912585               1   
5   Bronx  Kingsbridge  40.881687 -73.902818               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Caribbean Restaurant           Pizza Place              Pharmacy   
1  Caribbean Restaurant           Pizza Place                Bakery   
2  Caribbean Restaurant              Pharmacy           Pizza Place   
4           Pizza Place    Mexican Restaurant           Coffee Shop   
5           Pizza Place    Mexican Restaurant                  Park   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0                Bakery                 Diner                        Gym   
1         Grocery Store        Discount Store                   Pharmacy   
2                Bakery        Discount Store                      Diner   
4                  Café                  Park                     Bakery   
5                 Diner                  Café  Latin American Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop          Burger Joint    Seafood Restaurant   
1  Fast Food Restaurant    Italian Restaurant    Seafood Restaurant   
2         Grocery Store          Burger Joint         Shopping Mall   
4                 Diner             Wine Shop          Burger Joint   
5                Bakery           Coffee Shop            Donut Shop   

   10th Most Common Venue  
0      Italian Restaurant  
1    Gym / Fitness Center  
2  Furniture / Home Store  
4          Scenic Lookout  
5            Burger Joint

### Now, let's visualize the cluster on the map.

In [38]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]


In [39]:

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighborhood'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Now, I will examine the three clusters separately.

Let's see the 1st cluster which are in color Red in the above map. 
From the map, we could see that Cluster 1 located out of Manhatten Island and we can tell that within this cluster, most popular venues are Pizza Place, Mexican Restaurant and Parks.


In [40]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0           Wakefield  Caribbean Restaurant           Pizza Place   
1          Co-op City  Caribbean Restaurant           Pizza Place   
2         Eastchester  Caribbean Restaurant              Pharmacy   
45           Edenwald  Caribbean Restaurant           Pizza Place   
74           Canarsie  Caribbean Restaurant           Pizza Place   
75          Flatlands  Caribbean Restaurant           Pizza Place   
90          City Line           Pizza Place        Discount Store   
133      Howard Beach           Pizza Place    Italian Restaurant   
137     Richmond Hill           Pizza Place  Caribbean Restaurant   
146         Woodhaven           Pizza Place                 Diner   
147        Ozone Park           Pizza Place  Caribbean Restaurant   
148  South Ozone Park  Caribbean Restaurant           Pizza Place   
169          Rosedale  Caribbean Restaurant         Deli / Bodega   
170      Far Rockaway                 Beach           Pizza Place   
176          Edgemere                 Beach            Donut Shop   
187        Lindenwood           Pizza Place    Italian Restaurant   
188         Laurelton  Caribbean Restaurant            Donut Shop   
193        Brookville  Caribbean Restaurant        Clothing Store   
260          New Lots           Pizza Place        Discount Store   
261   Paerdegat Basin              Pharmacy           Pizza Place   

    3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
0                Pharmacy                     Bakery                 Diner   
1                  Bakery              Grocery Store        Discount Store   
2             Pizza Place                     Bakery        Discount Store   
45                 Bakery                   Pharmacy    Italian Restaurant   
74               Pharmacy                 Donut Shop        Discount Store   
75                 Bakery                   Pharmacy     Convenience Store   
90                 Bakery              Deli / Bodega           Supermarket   
133        Discount Store             Ice Cream Shop         Deli / Bodega   
137                Bakery                      Diner                 Plaza   
146             Pet Store             Ice Cream Shop                   Gym   
147                 Diner  Latin American Restaurant    Chinese Restaurant   
148    Italian Restaurant                Coffee Shop        Ice Cream Shop   
169            Donut Shop                Pizza Place  Fast Food Restaurant   
170    Chinese Restaurant                   Pharmacy         Grocery Store   
176           Pizza Place                  Surf Spot         Grocery Store   
187        Discount Store             Ice Cream Shop                 Diner   
188           Pizza Place       Fast Food Restaurant        Sandwich Place   
193            Donut Shop             Discount Store                  Park   
260  Caribbean Restaurant                   Pharmacy            Donut Shop   
261  Caribbean Restaurant                 Donut Shop     Convenience Store   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                          Gym        Ice Cream Shop          Burger Joint   
1                     Pharmacy  Fast Food Restaurant    Italian Restaurant   
2                        Diner         Grocery Store          Burger Joint   
45        Fast Food Restaurant                   Gym         Grocery Store   
74              Ice Cream Shop     Convenience Store            Bagel Shop   
75              Ice Cream Shop            Donut Shop           Coffee Shop   
90   Latin American Restaurant                 Diner            Donut Shop   
133                      Diner             Pet Store           Supermarket   
137         Italian Restaurant     Convenience Store         Grocery Store   
146        Japanese Restaurant        Cosmetics Shop    Chinese Restaurant   
147         Italian Restaurant        Ice Cream Shop  Gym / Fi

For Cluster 2 (purple dots on the map), we could tell that although most of the neighborhoods are out of the Manhatten Island but it's the only cluster that has neighborhoods within the Manhatten Island which is the most expensive place in NYC, while some are in Queens, some are in Brooklyn and some are in Staten Island.
And we this cluster of neighborhoods are more suitable for people who love Pizza Place while enjoy Chinese restaurant, Sushi Restaurant and Korean restaurant. 

In [41]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
4              Riverdale           Pizza Place         Mexican Restaurant   
5            Kingsbridge           Pizza Place         Mexican Restaurant   
6            Marble Hill    Mexican Restaurant                Pizza Place   
14    University Heights    Italian Restaurant                Pizza Place   
15        Morris Heights                  Park  Latin American Restaurant   
21            Mott Haven                  Park         Mexican Restaurant   
22           Port Morris                  Park         Mexican Restaurant   
26             Soundview           Pizza Place                       Park   
27          Clason Point                  Park                Pizza Place   
35        Spuyten Duyvil           Pizza Place         Mexican Restaurant   
40           Castle Hill           Pizza Place  Latin American Restaurant   
48           Sunset Park                Bakery                Pizza Place   
54              Flatbush  Caribbean Restaurant                       Café   
57            Kensington                  Park                       Café   
62              Bushwick                   Bar                Pizza Place   
80          Borough Park           Pizza Place         Mexican Restaurant   
93   Prospect Park South  Caribbean Restaurant                       Café   
101   Washington Heights                  Park                Pizza Place   
102               Inwood    Mexican Restaurant                Pizza Place   
221          Ditmas Park  Caribbean Restaurant                       Café   
299  Kingsbridge Heights           Pizza Place         Mexican Restaurant   

         3rd Most Common Venue      4th Most Common Venue  \
4                  Coffee Shop                       Café   
5                         Park                      Diner   
6                         Park                       Café   
14                        Café                     Bakery   
15                 Pizza Place         Mexican Restaurant   
21                        Café                Pizza Place   
22                        Café         Italian Restaurant   
26   Latin American Restaurant                      Diner   
27   Latin American Restaurant                Supermarket   
35                        Café                       Park   
40         American Restaurant                      Diner   
48          Mexican Restaurant                Coffee Shop   
54                 Pizza Place            Thai Restaurant   
57                         Bar                Coffee Shop   
62          Mexican Restaurant                Coffee Shop   
80                        Café            Thai Restaurant   
93                 Coffee Shop                       Park   
101  Latin American Restaurant           Tapas Restaurant   
102                       Café                       Park   
221                Coffee Shop                       Park   
299         Italian Restaurant  Latin American Restaurant   

         5th Most Common Venue      6th Most Common Venue  \
4                         Park                     Bakery   
5                         Café  Latin American Restaurant   
6    Latin American Restaurant                      Diner   
14          Mexican Restaurant                       Park   
15            Baseball Stadium                  Wine Shop   
21          Italian Restaurant              Grocery Store   
22                Tennis Court                Pizza Place   
26                 Supermarket        American Restaurant   
27                    Pharmacy             Discount Store   
35                      Bakery                Coffee Shop   
40          Mexican Restaurant         Spanish Restaurant   
48                        Café         Chinese Restaurant   
54                 Coffee Shop  Middle Eastern Restaurant   
57         American Restaurant       Caribbean Restaurant   
62                        Café                Yoga Studio  

What's interesting about cluster 3 is that most of the neighborhoods are far away from Manhatten Island and are crazy fan of Caribben Restaurant.

In [42]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood         1st Most Common Venue 2nd Most Common Venue  \
49             Greenpoint                        Bakery        Ice Cream Shop   
52         Sheepshead Bay              Sushi Restaurant            Bagel Shop   
61           Williamsburg                   Pizza Place   Japanese Restaurant   
77        Manhattan Beach              Sushi Restaurant                 Beach   
82        Gerritsen Beach              Sushi Restaurant            Bagel Shop   
85               Sea Gate  Theme Park Ride / Attraction            Theme Park   
96             North Side                   Coffee Shop           Pizza Place   
97             South Side                   Pizza Place           Coffee Shop   
115           Murray Hill             Korean Restaurant    Chinese Restaurant   
116               Chelsea            Italian Restaurant           Coffee Shop   
136           Kew Gardens                   Pizza Place  Caribbean Restaurant   
138              Flushing            Chinese Restaurant       Bubble Tea Shop   
144              Glendale                   Pizza Place                Bakery   
149         College Point            Chinese Restaurant         Deli / Bodega   
150            Whitestone             Korean Restaurant           Pizza Place   
152            Auburndale             Korean Restaurant            Bagel Shop   
153           Little Neck                   Pizza Place    Italian Restaurant   
154            Douglaston                   Pizza Place    Italian Restaurant   
155             Glen Oaks                        Bakery           Pizza Place   
158         Fresh Meadows                   Pizza Place     Korean Restaurant   
161       Oakland Gardens                   Pizza Place                  Park   
173              Steinway              Greek Restaurant                Bakery   
174            Beechhurst                 Deli / Bodega    Italian Restaurant   
180           Murray Hill             Korean Restaurant    Chinese Restaurant   
182            Holliswood                   Pizza Place                  Park   
183       Jamaica Estates                   Pizza Place     Indian Restaurant   
185             Hillcrest                   Pizza Place           Coffee Shop   
196  Forest Hills Gardens                   Pizza Place                Bakery   
201         West Brighton                   Pizza Place                   Bar   
205         Port Richmond                   Pizza Place    Italian Restaurant   
206      Mariner's Harbor                   Pizza Place    Italian Restaurant   
208     Castleton Corners                   Pizza Place    Italian Restaurant   
209       New Springville                Clothing Store    Italian Restaurant   
210                Travis                Clothing Store           Coffee Shop   
225           Westerleigh                   Pizza Place    Italian Restaurant   
226          Graniteville                   Pizza Place    Italian Restaurant   
227             Arlington                Clothing Store        Ice Cream Shop   
233            Grant City            Italian Restaurant           Pizza Place   
238          Butler Manor            Italian Restaurant           Pizza Place   
239            Charleston                   Pizza Place            Donut Shop   
243     Heartland Village                Clothing Store    Italian Restaurant   
244               Chelsea            Italian Restaurant           Coffee Shop   
246            Bulls Head            Italian Restaurant           Coffee Shop   
258              Elm Park                   Pizza Place        Ice Cream Shop   
264                Utopia                   Pizza Place                Bakery   
265               Pomonok                   Pizza Place    Chinese Restaurant   
284         Manor Heights            Italian Restaurant           Pizza Place   
285           Willowbrook                   Pizza Place            Bagel Shop   
286          Sandy Ground                   

# Results section


### So, we have three clusters after all.
### Within cluster 1, most popular venues are Pizza Place, Parks and Mexican Restrant. While its' locations are out of Manhatten.
### Within cluster 2, more Asian restaurants are avaiable and popular.
### Within cluster 3, more Carribean restaurants are there and it's far away from the Manhatten Island.

# Recommendation

It's really depends on the pet owner that what type of lifestyle they would like to have.
Cluster 1 are good for pet owners who are looking for more economic price neighborhood since it's not within Manhatten Island and parks are definitely a plus for dog owners.

Cluster 2 are highly recommended for people who are crazy for Asian restaurants and it has neighborhoods within Manhatten Island which are more high-end and luxury.

Cluster 3 are more suitable for people who love to stay in Brooklyn area and love Carribean restaurants.

# Future Improvement and Limitation

This analysis doesn't include the rental or house pricing data for different neighborhoods, it's more based on the popular venues and available pet services within neighborhoods. Thus it lacks the important info about the pricing which is the crucial factor when people are choosing for the neighborhoods.

Thus, it could be improved by getting listing price and rental price data into the k-means model.